# Mapping Food Access in New York City: Beyond the Supermarket
### Created By: Kyle Slugg

## Requirements:
    - secrets.py: A file containing keys for the Open Route Service API, Census Bureau API, and,  optionally, Mapbox API
    
   #### Data Retrieval and Processing
    - pandas
    - openrouteservice
    - requests
   
   #### Geodata Manipulation and Display
    - folium
    - shapely
    - geopandas

In [12]:
import secrets
import pandas as pd
import geopandas as gpd
import numpy as np
import time
import math
import folium
from folium.plugins import MarkerCluster
import requests
import json
from openrouteservice import client
import shapely

### Step One: Retrieve Fresh-Food Retailers from Open Street Map via Overpass API
Query to Overpass returns a list of geographic objects representing supermarkets, greengrocers, and grocery stores in New York City.

After retrieval, these objects are formatted as GeoJSON features, and ultimately written to disk as markets.json

In [2]:
overpass_url = "http://overpass-api.de/api/interpreter?"
overpass_query_markets = '''[out:json]
[timeout:25]
;
area(3600175905)->.searchArea;
(
  node
    ["shop"="supermarket"]
    (area.searchArea);
  way
    ["shop"="supermarket"]
    (area.searchArea);
  relation
    ["shop"="supermarket"]
    (area.searchArea);
  node
    ["shop"="grocery"]
    (area.searchArea);
  way
    ["shop"="grocery"]
    (area.searchArea);
  relation
    ["shop"="grocery"]
    (area.searchArea);
  node
    ["shop"="greengrocer"]
    (area.searchArea);
  way
    ["shop"="greengrocer"]
    (area.searchArea);
  relation
    ["shop"="greengrocer"]
    (area.searchArea);
);
out center;
>;
out skel qt;
'''

results = requests.get(url=overpass_url, params={'data':overpass_query}).json()

In [3]:
geographic_elements = {'type':'FeatureCollection',
                      'name':'markets',
                      'features':[]}

for element in results['elements']:
    if 'tags' in element:
        geodict = {'type':'Point'}
        propdict = {'id':element['id']}

        if element['type'] == 'node' and 'tags' in element:
            lon = element['lon']
            lat = element['lat']
            geodict['coordinates'] = [lon, lat]
            
        elif 'center' in element:
            lon = element['center']['lon']
            lat = element['center']['lat']
            geodict['coordinates'] = [lon, lat]
    
        for key, value in element['tags'].items():
            propdict[key] = value
        
        geographic_elements['features'].append({'type':'Feature',
                                   'geometry':geodict,
                                   'properties':propdict})

with open('./markets.json', 'w') as file:
    json.dump(geographic_elements, file, indent=2)
    

In [2]:
tracts = gpd.read_file('NYC_Tracts_Clipped.json')
markets = gpd.read_file('markets.json')
markets.head()

id                alt_name delivery drink:beer  \
0  419360013  Waverly Gourmet Market      yes        yes   
1  502791662                    None     None       None   
2  566894297                    None     None       None   
3  568230825                    None     None       None   
4  568230943                    None     None       None   

                   name                      opening_hours            phone  \
0  Waverly Urban Market  Mo-Sa 07:00-21:00; Su 08:00-21:00  +1-718-638-5454   
1               Yong Fa                               None             None   
2                  None                               None             None   
3  Aron's Kissena Farms                               None             None   
4               Keyfood                               None             None   

          shop addr:housenumber        addr:street  ... roof:shape  \
0  supermarket             None               None  ...       None   
1  supermarket            59-11        Main Street  ...       None   
2  supermarket             None               None  ...       None   
3  supermarket            72-15  Kissena Boulevard  ...       None   
4  supermarket             None               None  ...       None   

  building:levels building:min_level contact:instagram recycling:cans  \
0            None               None              None           None   
1            None               None              None           None   
2            None               None              None           None   
3            None               None              None           None   
4            None               None              None           None   

  recycling:glass recycling:plastic designation  type  \
0            None              None        None  None   
1            None              None        None  None   
2            None              None        None  None   
3            None              None        None  None   
4            None              None        None  None   

                     geometry  
0  POINT (-73.96646 40.68704)  
1  POINT (-73.82535 40.74343)  
2  POINT (-73.86297 40.82728)  
3  POINT (-73.81411 40.72842)  
4  POINT (-73.80451 40.73331)  

[5 rows x 129 columns]

In [5]:
#Pulling Census
CENSUS_KEY = secrets.CENSUS_API_KEY



In [21]:
#Implementing ORS Isochrones
ORS_KEY = secrets.ORS_API_KEY
ORS_URL = 'https://api.openrouteservice.org/v2/isochrones/foot-walking'

In [24]:
#Dividing lists into 5-location chunks

def divide_features(feature_df, n, geometry_col, id_col):
    '''TODO: Write Docstring'''
    ids_with_locations = {}

    feature_df['geom_reformat'] = feature_df[geometry_col].apply(lambda location: [location.x, location.y])
    
    df_chunks = np.array_split(feature_df[[id_col, 'geom_reformat']], math.trunc(feature_df.shape[0]/5)+1)
    
    for chunk in df_chunks:
        id_string = ''
        
        for item in chunk[id_col].tolist():
            id_string += f'{str(item)}_'
        
        location_list = chunk['geom_reformat'].tolist()
        
        ids_with_locations[id_string] = location_list
        

    return ids_with_locations

In [25]:
segments = divide_features(markets, 5, 'geometry', 'id')
print(segments)

{'419360013_502791662_566894297_568230825_568230943_': [[-73.9664572, 40.6870366], [-73.8253477, 40.743429], [-73.8629704, 40.827278], [-73.8141144, 40.7284202], [-73.8045119, 40.7333081]], '584125647_617378678_725335343_752186044_754498174_': [[-73.9913589, 40.7347925], [-73.9441156, 40.7141037], [-73.9294503, 40.8555109], [-73.9885326, 40.7317446], [-73.963094, 40.686808]], '889585036_897070965_910827450_999526102_1000798085_': [[-74.0117376, 40.7156112], [-73.8249882, 40.8808369], [-74.00622, 40.708147], [-73.9826745, 40.7683962], [-73.9862921, 40.7617166]], '1011407273_1038205809_1112494492_1252974601_1314445095_': [[-73.9817611, 40.780745], [-73.9822822, 40.7785184], [-73.989259, 40.7266467], [-73.8581219, 40.7111513], [-73.963651, 40.6761936]], '1314522027_1329106759_1383933476_1400462854_1491769924_': [[-74.0066439, 40.7371928], [-73.9892786, 40.7025998], [-73.9852324, 40.7688846], [-73.9642277, 40.7092394], [-73.9837784, 40.6767721]], '1599501273_1667353975_1682930317_168742033

In [ ]:
segments = divide_features(markets, 5, 'geometry', 'id')
print(segments)

params_iso = {'location_type':'destination',
          'range': [600, 420, 300], #420/60 = 7 mins
          'range_type': 'time',
          'attributes': ['area', 'reachfactor', 'total_pop'], # Get attributes for isochrones
          'smoothing': 5
         }

head_iso = {
    'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
    'Authorization': ORS_KEY,
    'Content-Type': 'application/json; charset=utf-8'
}

market_isochrones = {'type':'FeatureCollection',
                 'features':[]}

for id_string, locations in segments.items():
    params_iso['locations'] = locations
    params_iso['id'] = id_string
    id_list = np.repeat(id_string.split(sep='_'), len(params_iso['range']))
    
    try:
        isos = requests.post(ORS_URL, json=params_iso, headers=head_iso).json()

        i = 0
        for feature in isos['features']:
            feature['properties']['id'] = id_list[i]
            i += 1
            market_isochrones['features'].append(feature)
            print(feature)

    except:
        time.sleep(61)
        
        isos = requests.post(ORS_URL, json=params_iso, headers=head_iso).json()

        i = 0
        for feature in isos['features']:
            feature['properties']['id'] = id_list[i]
            i += 1
            market_isochrones['features'].append(feature)

with open('./market_isochrones.json', 'w') as file:
    json.dump(market_isochrones, file, indent=2)

In [9]:
#Splitting isochrone layer

isochrones = gpd.read_file('market_isochrones.json')

_5min_isos = isochrones[isochrones['value']==300]
_7min_isos = isochrones[isochrones['value']==420]
_10min_isos = isochrones[isochrones['value']==600]


_5min_isos.to_file("_5min_isos.geojson", driver='GeoJSON')
_7min_isos.to_file("_7min_isos.geojson", driver='GeoJSON')
_10min_isos.to_file("_10min_isos.geojson", driver='GeoJSON')


In [98]:
_5min_layer = _5min_isos.unary_union
_7min_layer = _7min_isos.unary_union
_10min_layer = _10min_isos.unary_union

In [126]:
#MAPBOX_KEY = secrets.MAPBOX_TOKEN

basemap = 'cartodbpositron'
m = folium.Map(location=[40.728783, -73.992320],
              tiles = basemap,
              zoom_start=11)

#Creating Clusters of Market Locations
market_clusters = MarkerCluster(name='Markets')
for geom, name in zip(markets['geometry'], markets['name']):
    folium.Marker(location = [geom.y, geom.x],
                 popup = name,
                 icon = folium.Icon(prefix='fa', icon='apple', 
                                    color='white', icon_color='red')).add_to(market_clusters)

m.add_child(market_clusters)

#Creating Isochron Layers

#FIGURE OUT HOW TO NEST


isochron_layers = folium.map.FeatureGroup(name='Walking Time')
m.add_child(isochron_layers)

_10min = folium.plugins.FeatureGroupSubGroup(isochron_layers, '10 min.')
m.add_child(_10min)

_7min = folium.plugins.FeatureGroupSubGroup(isochron_layers, '7 min.')
m.add_child(_7min)

_5min = folium.plugins.FeatureGroupSubGroup(isochron_layers, '5 min.')
m.add_child(_5min)


_10min.add_child(folium.GeoJson(_10min_layer, name='10 min.', style_function = lambda x: 
                                {'fillColor': 'red',
                                 'fillOpacity': 1,
                                 'weight': 1,
                                 'color': 'black'
                                }))
_7min.add_child(folium.GeoJson(_7min_layer, name='7 min.', style_function = lambda x: 
                                {'fillColor': 'yellow',
                                 'fillOpacity': 1,
                                 'weight': 1,
                                 'color': 'black'
                                }))
_5min.add_child(folium.GeoJson(_5min_layer, name='5 min.', style_function = lambda x: 
                                {'fillColor': 'green',
                                 'fillOpacity': 1,
                                 'weight': 1,
                                 'color': 'black'
                                }))


#Tract Layers
tract_layer = 'NYC_Tracts_Clipped.json'

def tract_style_function(feature):
    return{
        'fillOpacity': 0.5,
        'weight': 1,
        'fillColor':'#d5f78b',
        'color':'#3d3d3d'}

folium.GeoJson(tract_layer,
              name='Census Tracts',
              style_function = tract_style_function, overlay=False).add_to(m)

folium.LayerControl().add_to(m)

In [127]:
m